In [82]:
import random
import copy
from load import *
import load
import networkx as nx
import matplotlib.pyplot as plt

In [83]:
g=load.load_random_hetero_graph('../data/PAAD_network', Specified_quantity={'lncrna': 1500, 'mirna': 168, 'mrna': 2519})
adjacency_matrix=torch.from_numpy(np.array(nx.adjacency_matrix(dgl.to_homogeneous(g).to_networkx().to_undirected()).todense(),dtype=float))
gragh = nx.Graph()
for i in range(len(adjacency_matrix)):
    gragh.add_node(i)
    gragh.nodes[i]["data"] = i

for i in range(len(adjacency_matrix)):
    for j in range(len(adjacency_matrix)):
        if adjacency_matrix[i,j]:
            gragh.add_edge(i,j)


Graph(num_nodes={'lncrna': 1500, 'mirna': 168, 'mrna': 2519},
      num_edges={('lncrna', 'lnc_lnc', 'lncrna'): 12654, ('lncrna', 'lnc_mi', 'mirna'): 186, ('lncrna', 'm_lnc', 'mrna'): 23276, ('mirna', 'mi_lnc', 'lncrna'): 186, ('mirna', 'mi_m', 'mrna'): 17320, ('mirna', 'mi_mi', 'mirna'): 132, ('mrna', 'lnc_m', 'lncrna'): 23276, ('mrna', 'm_m', 'mrna'): 60230, ('mrna', 'm_mi', 'mirna'): 17320},
      metagraph=[('lncrna', 'lncrna', 'lnc_lnc'), ('lncrna', 'mirna', 'lnc_mi'), ('lncrna', 'mrna', 'm_lnc'), ('mirna', 'lncrna', 'mi_lnc'), ('mirna', 'mrna', 'mi_m'), ('mirna', 'mirna', 'mi_mi'), ('mrna', 'lncrna', 'lnc_m'), ('mrna', 'mrna', 'm_m'), ('mrna', 'mirna', 'm_mi')])


In [84]:
#画图
# plt.subplot(211)
# nx.draw_networkx(gragh, with_labels=True,node_size=50,font_size=8)
# plt.show()

In [85]:
#去掉真实网络中去点度为0的孤立节点
new_nodes = [_ for _, v in nx.degree(gragh) if v != 0]

# plt.subplot(211)
graph_new = gragh.subgraph(new_nodes)
# nx.draw_networkx(graph_new, with_labels=True,node_size=50,font_size=8)
# plt.show()


In [86]:
print(len(new_nodes))

3217


In [87]:
#对联通子图进行判断
# N = 50
# N = 100
# N = 150
# N = 200
# N = 250
N = 300
idex = 3
CS = []
CS_len = []
init_graph = []
for c in nx.connected_components(graph_new):
    # 得到不连通的子集
    nodeSet = list(graph_new.subgraph(c).nodes())
    CS.append(c)
    CS_len.append(len(nodeSet))
    if len(nodeSet) <N:
        init_graph.append(nodeSet)
print(CS_len)
graph_new = graph_new.subgraph(CS[0])
#小于N的，直接算子图
#大于N的，直接进行采样

[3164, 2, 2, 2, 3, 2, 3, 2, 2, 2, 2, 2, 2, 2, 3, 2, 2, 2, 2, 2, 2, 4, 2, 2, 2]


In [88]:
print(graph_new.nodes())
#获取新图的节点
new_sort_nodes = list(graph_new.nodes())
node_dict = {}
node_dict_reverse = {}
#记录新节点在邻接矩阵中的index下标
for i,n in enumerate(new_sort_nodes):
    node_dict[n] = i
    node_dict_reverse[i] = n
new_A=np.array(nx.adjacency_matrix(graph_new).todense())
#改变邻接矩阵
print(new_A)

[0, 2, 4, 5, 6, 7, 8, 9, 16, 19, 20, 22, 23, 24, 30, 31, 32, 34, 36, 38, 39, 46, 52, 53, 54, 55, 59, 60, 63, 64, 65, 66, 71, 78, 80, 81, 82, 83, 86, 87, 95, 98, 101, 102, 103, 104, 105, 108, 112, 117, 121, 122, 123, 125, 126, 135, 138, 139, 140, 142, 144, 145, 146, 148, 149, 150, 154, 163, 165, 166, 170, 171, 173, 178, 180, 185, 188, 189, 194, 200, 203, 204, 205, 206, 208, 210, 212, 213, 215, 218, 219, 220, 222, 224, 225, 226, 229, 232, 236, 238, 240, 241, 242, 244, 245, 254, 256, 262, 263, 264, 265, 267, 268, 270, 272, 275, 282, 283, 287, 288, 292, 299, 301, 304, 305, 306, 307, 308, 312, 314, 316, 319, 321, 322, 327, 328, 332, 334, 337, 339, 346, 347, 350, 358, 359, 360, 362, 364, 366, 367, 369, 376, 379, 381, 382, 385, 388, 389, 395, 396, 397, 398, 399, 402, 403, 405, 409, 411, 412, 418, 421, 422, 423, 424, 425, 427, 428, 429, 430, 433, 437, 439, 441, 442, 443, 444, 445, 451, 452, 453, 454, 455, 456, 457, 458, 459, 461, 462, 463, 469, 472, 474, 475, 476, 482, 483, 484, 490, 491, 493,

In [89]:
print(len(new_A))
print(680 in node_dict.keys())

3164
False


In [90]:
#首先需要获取所有节点的邻居集合
node_neigh = {}
for i in range(len(new_A)):
    for j in range(len(new_A)):
        if new_A[i,j]:
            if node_dict_reverse[i] not in node_neigh.keys():
                node_neigh[node_dict_reverse[i]] = [node_dict_reverse[j]]
            else:
                node_neigh[node_dict_reverse[i]].append(node_dict_reverse[j])
print(node_neigh)

{0: [39, 220, 254, 362, 532, 937, 959, 1003, 1059, 1206, 1242, 1253, 1259, 2034, 2063, 2335, 2458, 2566, 2624, 2892, 2929, 2930, 3018, 3202, 3223, 3243, 3253, 3290, 3755, 3814, 3845, 3889, 4013], 2: [4035], 4: [5, 30, 54, 59, 66, 319, 445, 522, 561, 614, 755, 773, 786, 787, 788, 796, 882, 916, 1015, 1048, 1109, 1128, 1142, 1215, 1230, 1325, 1362, 1375, 1393, 1692, 1827, 1883, 1897, 1913, 2037, 2054, 2067, 2068, 2164, 2196, 2216, 2220, 2271, 2347, 2425, 2427, 2467, 2476, 2623, 2729, 2784, 2815, 2896, 2897, 3010, 3050, 3203, 3326, 3509, 3551, 3579, 3634, 3737, 3847, 3887, 3897, 3944, 3990, 4041, 4154], 5: [4, 59, 319, 522, 561, 755, 796, 921, 1050, 1128, 1140, 1215, 1325, 2054, 2067, 2068, 2220, 2271, 2427, 2467, 2729, 3010, 3509, 3897], 6: [7, 306, 307, 376, 457, 572, 758, 1172, 1311, 1378, 1849, 2591, 2837, 3187, 3577, 3952], 7: [6, 457, 1172, 1311, 1312, 1798, 3154, 3187, 3610, 3636, 3900, 4143], 8: [2882], 9: [4164, 4172], 16: [1108, 1360, 2228, 3612], 19: [545, 602, 1273, 1759, 1849

In [91]:
#需要对把新节点按度排序
degree_list = [(node,v) for node, v in nx.degree(graph_new) ]
nodes_degree_dict = {}
for node,degree in degree_list:
    nodes_degree_dict[node] = degree
# print(degree_list)
degree_sorted_nodes = sorted(degree_list,key=lambda x: x[1],reverse=True)
# degree_sorted_nodes = sorted(degree_list,key=lambda x: x[1])
print(degree_sorted_nodes)

[(1582, 514), (1518, 501), (1526, 451), (1565, 450), (1530, 432), (1537, 426), (1529, 395), (1548, 385), (1595, 385), (3598, 367), (4012, 366), (4120, 366), (2801, 364), (1620, 356), (1528, 350), (1821, 350), (3227, 348), (2800, 347), (1641, 345), (1896, 345), (1897, 345), (3078, 341), (3448, 339), (1827, 337), (2866, 336), (4154, 336), (1692, 334), (2847, 334), (4150, 332), (2451, 329), (1738, 328), (3057, 328), (3421, 328), (3507, 328), (3520, 328), (484, 324), (2623, 320), (1048, 316), (3887, 313), (1640, 312), (3542, 311), (3684, 309), (3944, 308), (1574, 304), (3800, 304), (1779, 303), (2060, 301), (3307, 301), (3688, 301), (2054, 300), (3427, 300), (2896, 295), (1109, 294), (2425, 293), (1364, 292), (2897, 292), (3930, 292), (2204, 291), (497, 290), (916, 290), (3509, 290), (3376, 289), (4041, 288), (1393, 287), (1913, 285), (1142, 284), (2784, 284), (3882, 284), (740, 283), (3182, 283), (3551, 283), (3634, 283), (3847, 283), (561, 281), (1867, 281), (1909, 278), (3008, 278), (21

In [92]:
#写一个函数，输入为list[node,...,],输出为按照度排序的list，相同degree要随机打乱，每次生成结果不同
def get_degree_sorted_list(nodes):
    #按度排序好
    nodes = sorted(nodes,key=lambda x:nodes_degree_dict[x])
    degree_sorted_nodes = [(node,nodes_degree_dict[node]) for node in nodes]
    #相同度要随机打乱
    dict_degree = {}
    #获取各个degree的list集合
    for node,degree in degree_sorted_nodes:
        if degree not in dict_degree.keys():
            dict_degree[degree] = [node]
        else:
            dict_degree[degree].append(node)
    #将各个list随机打乱，然后按度拼接在一起
    for degree,node_list in dict_degree.items():
        random.shuffle(dict_degree[degree])
    dict_degree_key = sorted(dict_degree.keys(),reverse=True)
    sorted_nodes = []
    for key in dict_degree_key:
        sorted_nodes.extend(dict_degree[key])
    return sorted_nodes
    

In [93]:
nodes = [node for node_ in degree_list]
sorted_nodes = get_degree_sorted_list(nodes)
#将度相同节点随机打乱
# all_nodes_divide_by_degree = []
# dict_degree = {}
# #获取各个degree的list集合
# for node,degree in degree_sorted_nodes:
#     if degree not in dict_degree.keys():
#         dict_degree[degree] = [node]
#     else:
#         dict_degree[degree].append(node)
# #将各个list随机打乱，然后按度拼接在一起
# for degree,node_list in dict_degree.items():
#     random.shuffle(dict_degree[degree])
# dict_degree_key = sorted(dict_degree.keys(),reverse=True)
# sorted_nodes = []
# for key in dict_degree_key:
#     sorted_nodes.extend(dict_degree[key])
# print(len(sorted_nodes))


In [94]:
#使用随机游走采样方法
#按照度由大到小的顺序进行采样，直到满足终止条件
#采样终止条件是所有节点都被采样到
# nodes_if_choosed = [0] * len(new_sort_nodes)
# all_subgraph = []
# cursor = 0
# while sum(nodes_if_choosed) != len(new_sort_nodes):
#     sub_graph = set([])
#     node = random.randint(0,len(new_sort_nodes)-1)
#     while node in sub_graph:
#         node = random.randint(0,len(new_sort_nodes)-1)
#     sub_graph.add(node_dict_reverse[node])
#     nodes_if_choosed[node] = 1
#     while len(sub_graph) != N:
# 
#         #随机选一个邻居加入子图中
#         neigh_nodes = node_neigh[node_dict_reverse[node]]
#         node = random.choice(neigh_nodes)
# 
#         sub_graph.add(node)
#         nodes_if_choosed[node_dict[node]] = 1
#         node = node_dict[node]
# 
#     all_subgraph.append(list(sub_graph))
#     print(list(sub_graph))
print(len(sorted_nodes))

3164


In [95]:
#用K阶邻居采样
#N表示每个子图大小
#按照度由大到小的顺序进行采样，直到满足终止条件
#按照度由小到大的顺序进行采样，直到满足终止条件
#采样终止条件是所有节点都被采样到
nodes_if_choosed = [0] * len(sorted_nodes)
all_subgraph = []
cursor = 0
while sum(nodes_if_choosed) != len(sorted_nodes):
    sub_graph = []
    #从new_sort_nodes，随机产生一个节点，生成K阶邻居
    node = degree_sorted_nodes[cursor][0]
    cursor+=1
    sub_graph.append(node)
    now_nodes = [node]
    neigh_nodes_k = []
    for n in now_nodes:
        neigh_nodes_k.extend(node_neigh[n])
    nodes_if_choosed[node_dict[node]] = 1
    #开始添加node的K阶邻居，直到数量达到N
    while len(set(sub_graph)) != N:
        #先判断现有节点+新K-阶邻居节点够不够达到N，不够直接全加，否则按度分布加
        nodes_can_add = [node for node in neigh_nodes_k]
        if (len(sub_graph)+len(set(nodes_can_add))) <=N:
            for n in nodes_can_add:
                nodes_if_choosed[node_dict[n]] = 1
                sub_graph.append(n)
            # sub_graph.extend(nodes_can_add)
        else:
            #邻居节点按照度排序
            new_sorted_nodes = get_degree_sorted_list(list(set(nodes_can_add)))
            print(len(sub_graph))
            for n in new_sorted_nodes:
                nodes_if_choosed[node_dict[n]] = 1
                sub_graph.append(n)
                if len(set(sub_graph)) == N:
                    break
        now_nodes = neigh_nodes_k.copy()
        neigh_nodes_k = []
        for n in now_nodes:
            neigh_nodes_k.extend(node_neigh[n])
        
    all_subgraph.append(list(set(sub_graph)))
    print(list(set(sub_graph)))

1
[2560, 2561, 4098, 3074, 2052, 3077, 2054, 2055, 2053, 3081, 4108, 2063, 3087, 2067, 2581, 3606, 4120, 2072, 3096, 3099, 3612, 3614, 2591, 4127, 3109, 3621, 4135, 2600, 3624, 3627, 2605, 1582, 2094, 4141, 2097, 3634, 4148, 2104, 4153, 4154, 2105, 2106, 2107, 3645, 3643, 3575, 2628, 3141, 2122, 2123, 3658, 3661, 3577, 3664, 3153, 3666, 4180, 3157, 2135, 4183, 2649, 3162, 2651, 2140, 3677, 2139, 2655, 3169, 2663, 2152, 3692, 2671, 3696, 625, 3185, 2675, 3188, 2678, 2679, 4094, 2681, 2174, 3199, 2175, 3710, 2695, 3719, 2186, 2700, 3213, 3726, 1680, 3728, 3219, 1683, 3732, 3736, 3737, 3228, 3744, 2210, 3747, 3236, 2220, 1710, 2735, 3248, 2737, 3762, 2230, 1719, 3256, 2233, 2746, 2750, 3262, 3267, 3780, 3781, 1734, 3783, 1737, 3793, 2771, 3796, 2261, 2775, 1752, 2783, 2786, 3814, 2793, 1773, 1779, 1781, 1782, 3322, 2813, 3329, 2306, 3843, 2308, 1798, 3336, 2313, 2824, 2827, 2316, 1806, 2831, 2320, 3860, 1813, 3862, 2838, 3352, 2841, 2324, 3867, 2335, 1824, 3871, 2338, 3874, 2849, 3876, 38

In [96]:
print(len(all_subgraph))

3162


In [97]:
nodes_nums = {}
#子图数量可能会太多，删掉重复的
for subgraph in all_subgraph[::-1]:
    for n in subgraph:
        if n not in nodes_nums.keys():
            nodes_nums[n] = 1
        else:
            nodes_nums[n] = nodes_nums[n] + 1
if_del = []

# for subgraph in all_subgraph[::-1]:
#     flag = 1
#     for n in subgraph:
#         #不能删
#         if nodes_nums[n] <=1 :
#             flag = 0
#     if_del.append(flag)

In [98]:
print(if_del)
print(len(nodes_nums))

[]
3164


In [99]:
del_all_graph = copy.deepcopy(all_subgraph[::-1])
not_del = 0
for index,subgraph in enumerate(all_subgraph[::-1]):
    print(index)
    #遍历所有的子图，判断能不能删除，能删除就当场删除，并重新计算nodes_nums
    flag = 1
    for n in subgraph:
        #不能删
        if nodes_nums[n] <=1 :
            flag = 0  
            break
    if flag:
        del_all_graph.pop(not_del)
    else:
        not_del+=1
    # print(len(del_all_graph),'*')
    nodes_nums = {}
    #子图数量可能会太多，删掉重复的
    for subgraph in del_all_graph:
        for n in subgraph:
            if n not in nodes_nums.keys():
                nodes_nums[n] = 1
            else:
                nodes_nums[n] = nodes_nums[n] + 1


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [100]:
print(len(del_all_graph))
# print(del_all_graph)

352


In [101]:
nodes_nums = {}
#子图数量可能会太多，删掉重复的
for subgraph in del_all_graph:
    for n in subgraph:
        if n not in nodes_nums.keys():
            nodes_nums[n] = 1
        else:
            nodes_nums[n] = nodes_nums[n] + 1
print(nodes_nums)

{2560: 73, 2561: 45, 4098: 91, 3074: 54, 2052: 71, 3077: 55, 2054: 232, 2055: 150, 2053: 44, 3081: 81, 4108: 188, 2063: 78, 3087: 122, 2067: 204, 2581: 24, 3606: 99, 4120: 311, 2072: 127, 3096: 55, 3099: 69, 3612: 33, 3614: 197, 2591: 98, 4127: 37, 3109: 25, 3621: 31, 4135: 47, 2600: 98, 3624: 44, 3626: 11, 3627: 66, 2605: 49, 1582: 246, 2094: 171, 4141: 82, 2097: 43, 3634: 196, 4148: 41, 2104: 36, 4153: 168, 4154: 265, 2105: 262, 2106: 160, 4157: 1, 2107: 55, 3645: 28, 3643: 35, 3575: 83, 2628: 37, 3141: 86, 2122: 135, 2123: 56, 3658: 36, 3661: 87, 3577: 72, 3664: 155, 3153: 71, 3666: 35, 4180: 130, 3157: 34, 2135: 180, 2649: 136, 3162: 29, 2651: 159, 2140: 69, 3677: 36, 2139: 28, 2655: 81, 3169: 114, 2663: 93, 2152: 152, 3692: 268, 2671: 117, 3696: 63, 625: 56, 3185: 81, 2675: 45, 3188: 185, 2678: 71, 2679: 67, 4094: 65, 2681: 42, 2174: 225, 3199: 117, 2175: 126, 3710: 78, 2695: 41, 3719: 48, 2186: 80, 2700: 51, 3213: 59, 3726: 139, 1680: 44, 3728: 27, 3219: 56, 1683: 77, 3732: 37, 3

In [102]:
#再把节点数小于N的联通子图加上
# for c in init_graph:
#     c.extend([-1]*(N-len(c)))
# print(init_graph)

In [103]:
# del_all_graph.extend(init_graph)

In [104]:
# del_all_graph.pop(-1)
print(del_all_graph[len(del_all_graph)-1])

[4096, 3585, 3074, 2563, 3588, 3077, 2053, 2055, 2567, 3590, 3595, 3089, 3091, 3093, 3097, 3609, 3099, 2076, 3100, 3616, 4128, 3108, 1574, 3110, 4139, 3115, 4141, 2609, 2610, 3124, 3636, 4148, 2104, 2105, 3130, 3643, 2620, 2556, 2110, 4160, 3649, 2625, 2113, 4165, 3655, 4169, 3662, 2638, 3153, 3666, 2131, 4178, 3669, 3670, 2647, 2648, 2654, 2144, 2657, 3169, 2656, 2659, 2661, 3696, 3698, 3188, 2676, 2678, 3708, 3709, 3711, 3715, 2181, 1671, 3719, 3209, 2698, 2190, 2707, 2196, 3222, 3223, 3736, 2202, 3739, 1694, 3745, 2210, 3747, 2723, 2213, 2721, 2212, 3752, 1707, 3756, 2733, 2735, 2736, 1714, 2740, 2230, 3256, 3769, 1722, 2748, 3260, 2750, 3775, 2752, 3778, 2242, 1735, 2759, 3785, 1737, 2762, 3276, 3790, 3796, 3797, 2773, 3799, 2265, 1754, 2778, 2268, 2269, 1758, 3295, 2272, 2273, 3303, 2280, 3306, 2795, 2798, 2287, 2800, 3824, 2803, 2292, 2293, 2806, 1783, 2296, 2810, 1788, 1789, 3326, 3839, 3842, 2306, 2307, 2310, 2822, 3336, 2825, 2824, 2827, 3851, 2829, 2318, 3342, 3341, 3345, 385

In [105]:
import pandas as pd
data = pd.DataFrame(del_all_graph)
data.head()

0     1     2     3     4     5     6     7     8     9    ...   290  \
0  2560  2561  4098  3074  2052  3077  2054  2055  2053  3081  ...  2033   
1  4097  2563  3077  2053  2055  3595  2059  2577  3603  3093  ...  2034   
2  4097  2563  3077  2053  2055  3595  2059  2577  3603  3093  ...  2034   
3  3074  3075  2563  4100  3596  2573  2574  4111  3768  3602  ...  2023   
4  4096  2544  3074  4099  2564  2054  3081  4105  3596  4109  ...  2034   

    291   292   293   294   295   296   297   298   299  
0  3058  2034  2542  2039  3576  2041  2042  2045  2558  
1  2545  2036  4085  4080  2551  2040  2548  2042  3059  
2  2545  2036  4085  4080  2551  2040  2548  2042  3059  
3  2540  2030  4080  4085  3065  2042  3067  3069  3071  
4  2545  2036  4085  4084  2550  2040  2041  2045  3582  

[5 rows x 300 columns]

In [106]:
print(len(del_all_graph))

352


In [107]:
data.to_csv("../data/SubGraph/N"+str(N)+"/N"+str(N)+"_"+str(idex)+"_"+str(len(del_all_graph))+".csv",index=False)

In [108]:
data = pd.read_csv("../data/SubGraph/N"+str(N)+"/N"+str(N)+"_"+str(idex)+"_"+str(len(del_all_graph))+".csv")
data.head()

0     1     2     3     4     5     6     7     8     9  ...   290  \
0  2560  2561  4098  3074  2052  3077  2054  2055  2053  3081  ...  2033   
1  4097  2563  3077  2053  2055  3595  2059  2577  3603  3093  ...  2034   
2  4097  2563  3077  2053  2055  3595  2059  2577  3603  3093  ...  2034   
3  3074  3075  2563  4100  3596  2573  2574  4111  3768  3602  ...  2023   
4  4096  2544  3074  4099  2564  2054  3081  4105  3596  4109  ...  2034   

    291   292   293   294   295   296   297   298   299  
0  3058  2034  2542  2039  3576  2041  2042  2045  2558  
1  2545  2036  4085  4080  2551  2040  2548  2042  3059  
2  2545  2036  4085  4080  2551  2040  2548  2042  3059  
3  2540  2030  4080  4085  3065  2042  3067  3069  3071  
4  2545  2036  4085  4084  2550  2040  2041  2045  3582  

[5 rows x 300 columns]